In [1]:
import requests
from bs4 import BeautifulSoup
import string
from datetime import datetime
import pandas as pd
import json

C:\Users\linds\anaconda3\lib\site-packages\requests\__init__.py:89: RequestsDependencyWarning: urllib3 (1.26.7) or chardet (3.0.4) doesn't match a supported version!
  warnings.warn("urllib3 ({}) or chardet ({}) doesn't match a supported "


In [2]:
pd.set_option('display.max_rows', None)

In [3]:
# Woman's page
woman = "https://ecoalf.com/en/women-100"

In [4]:
def get_category(url):
    output_list = list()
    page = BeautifulSoup(requests.get(url).content,'lxml')
    # Find all the div classes associated with a clothes category
    category_class = page.find_all('div',class_="elementor-iqit-banner")
    
    # Create an empty category dictionary to store category name and link
    category_dict = {}
    for item in category_class:
        try:
            # Retrieve category name
            c = item.find('div').get_text()
        except:
            c = None
        # Retrieve category link
        l = item.find('a').get('href')
        if "de" in l:
            l = l.replace("de", "en")

        # Store the name-link pair in category dictionary
        category_dict[str(c)]=l
    
    # Loop through each category in the dictionary
    for category, link in category_dict.items():
        
        # Run get_product function on each category page to retrieve individual product
        lst = get_product(category,link)
        
        # Append to output list
        output_list.extend(lst)
        
    # Create dataframe
    df = pd.DataFrame(output_list, columns =['display_name','product_material','color','size','price','product_url','image_link_color','brand_name','description','scrapped_date','low_level','gender','secondhand'])
    return df


In [5]:
def get_product(category, category_link):
    page = BeautifulSoup(requests.get(category_link).content,'lxml')
    # Find all the div classes associated with a product
    product_class = page.find_all('div',class_="thumbnail-container")
    
    # Create an empty list to store products
    products = []
    
    # Create an empty category dictionary to store product name and link
    product_dic = {}
    for item in product_class:
        try:
            # Retrieve product name
            p = item.find("img").get("alt")
        except:
            p = None
        # Retrieve product link
        l = item.find('a').get('href')
        if "women" in l or "woman" in l:
            # Store the name-link pair in category dictionary
            product_dic[str(p)]=l
    
    # Loop through each product in the dictionary
    for product, link in product_dic.items():
        
        # Store brand_name
        brand_name = "ecoalf"
        # Store scrapped_date
        scrapped_date = datetime.today().strftime('%Y-%m-%d')
        # Store gender
        gender = "Woman"
        # Store secondhand
        secondhand = "No"
        
        # Run get_details function on each product page to retrieve details on each individual product
        product_material, color, image_link_color, size, price, description = get_details(link)
        
        # Append the new product to the products list
        products.append([product,product_material,color,size,price,link,image_link_color,brand_name,description,scrapped_date,category,gender,secondhand])
    
    return products
   

In [6]:
def get_details(product_link):
    page = BeautifulSoup(requests.get(product_link).content,'lxml')
    
    # Retrieve product materials
    details = page.find('div', class_="product-description-short rte-content").find_all('li')
    # Create an empty product_material dictionary
    product_material = {}
    for item in details:
        text = item.get_text()
        if "Main fabric" in text:
            materials = text.strip().split("Main fabric: ")[1].split(" / ")
            for item in materials:
                pct = item.split('%')[0]
                pct = f'{pct}%'
                mtr = item.split('%')[1]
                product_material[str(mtr)]=pct
    product_material = json.dumps(product_material)
    
    # Create an empty color list
    color = []
    # Create an empty image_link_color dictionary
    image_link_color = {}
    # Retrieve available colors if multiple colors are offered
    try:
        color_class = page.find('div', class_="block-content d-flex justify-content-center justify-content-md-start mb-2 mt-3").find_all('a')
        for item in color_class:
            link = item.get('href')
            image = BeautifulSoup(requests.get(link).content,'lxml').find('div', class_="product-lmage-large swiper-slide").find('a').get('href')
            c = item.get('title').strip()
            # Store available colors in color list
            color.append(c)
            # Store color-link pairs in image_link_color dictionary
            image_link_color[str(c)]=image
            
    # Retrieve single color if only single color is offered
    except:
        c = page.find('div',class_="nomcolor text-capitalize mb-4 text-center text-md-left").get_text()
        color.append(c)
        try:
            image = page.find('div', class_="product-lmage-large swiper-slide").find('a').get('href')
            image_link_color[str(c)]=image
        except:
            image_link_color[str(c)]=None
    color = json.dumps(color)
    image_link_color = json.dumps(image_link_color)
    
        
    # Retrieve available sizes
    size_class = page.find_all('li',class_="input-container float-left")
    # Create an empty size list
    size = []
    for item in size_class:
        s = item.find('span').get_text()
        size.append(s)
    size = json.dumps(size)
        
    # Retrieve price
    price = page.find('span', class_="product-price").get_text()
    price = price.split('$')[1]
    price = f'USD {price}'
    
    # Retrieve description
    description = page.find('div',class_="product-description text-left").find('div',class_="rte-content").get_text().strip()
        
    return product_material, color, image_link_color, size, price, description

In [7]:
df_woman = get_category(woman)

In [8]:
df_woman

display_name  \
0                Mandu Jacket Woman   
1                  Lenox Long Woman   
2                  Asp Jacket Woman   
3              Marangu Jacket Woman   
4              Amu New Jacket Woman   
5                Gedre Jacket Woman   
6              Glacier Jacket Woman   
7                Marangu Vest Woman   
8             Mulhacen Woman Jacket   
9       Noir Reversible Oversize...   
10                 Uma Jacket Woman   
11     Sarrau Corduroy Jacket Woman   
12                 Tao Jacket Woman   
13             Ushuaia Jacket Woman   
14          New Croset Jacket Woman   
15    Vintage Diamonds Jacket Woman   
16             Esterri Jacket Woman   
17         Arties Vest Woman Jacket   
18                Snow Jacket Woman   
19               Tera Jacket  Woman   
20               Sagra Jacket Woman   
21              Mountain Woman Vest   
22                   Odra Top Woman   
23                Pino Jersey Woman   
24          Pino Round Woman Jersey   
25                 Val Sleeve Woman   
26     Vielha Turtle Seamless Woman   
27      Vielha Round Seamless Woman   
28                Riaza Woman Dress   
29            Tormes Woman Cardigan   
30               Cea Oversize Woman   
31                Inma Jersey Woman   
32               Tera Jacket  Woman   
33          Baiona Woman Sweatshirt   
34          Llanes Because Woman...   
35               Basic Woman Hoodie   
36                Aldan Woman Sweat   
37         Getaria Woman Sweatshirt   
38         Bolonia Woman Sweatshirt   
39       Cudillero Woman Sweatshirt   
40        Fornells Woman Sweatshirt   
41   Llanes Choice Woman Sweatshirt   
42            Lulu Woman Sweatshirt   
43      Acacia Woman Long Sleeve...   
44              Lavanda Shirt Woman   
45                 Wolf Shirt Woman   
46        Magnolia Long Shirt Woman   
47      Cortegana Woman Long Sleeve   
48            Because Woman T-Shirt   
49       Cadaques Woman Long Sleeve   
50            Mundaca Woman T-Shirt   
51    Choice Long Sleeve T-Shirt...   
52       Ecoalf Since Woman T-Shirt   
53            Great B Woman T-Shirt   
54                 Cega Pants Woman   
55             Penelope Woman Pants   
56                Nanga Pants Woman   
57                Patri Woman Pants   
58          Samani Pant-Skirt Woman   
59                Adaja Pants Woman   
60                 Arce Pants Woman   
61                Riaza Woman Dress   
62                 Noja Dress Woman   
63         Gabriel Long Dress Woman   
64                 Mery Woman Dress   
65          Nogal  Long Dress Woman   
66                Tahoe Dress Woman   
67            Olmo Belt Skirt Woman   
68                 Etna Skirt Woman   
69          Samani Pant-Skirt Woman   
70            Guadalupe Skirt Woman   
71                Mont  Dress Woman   
72                'BECAUSE' LEGGING   
73   Spoo Medium Size Shopper Woman   
74                       Samara Bag   
75            Olmo Belt Skirt Woman   
76              Mountain Woman Vest   
77      Spoo Big Size Shopper Woman   
78                 Etna Skirt Woman   
79         Arties Vest Woman Jacket   
80               Cea Oversize Woman   
81            Guadalupe Skirt Woman   
82            Tormes Woman Cardigan   
83                Inma Jersey Woman   
84                Snow Jacket Woman   
85          Samani Pant-Skirt Woman   
86             Esterri Jacket Woman   
87                Adaja Pants Woman   
88             Jonic Sneakers Woman   
89              Jonic Slip On Woman   
90                 Wolf Shirt Woman   
91               Tera Jacket  Woman   
92                Mont  Dress Woman   
93        Magnolia Long Shirt Woman   
94               Sagra Jacket Woman   
95                 Arce Pants Woman   
96         Getaria Woman Sweatshirt   
97          Llanes Because Woman...   
98            Because Woman T-Shirt   
99    Choice Long Sleeve T-Shirt...   
100           Great B Woman T-Shirt   

                                      produc

In [9]:
# Man's page
man = "https://ecoalf.com/en/men-200"

In [10]:
def get_product(category, category_link):
    page = BeautifulSoup(requests.get(category_link).content,'lxml')
    # Find all the div classes associated with a product
    product_class = page.find_all('div',class_="thumbnail-container")
    
    # Create an empty list to store products
    products = []
    
    # Create an empty category dictionary to store product name and link
    product_dic = {}
    for item in product_class:
        try:
            # Retrieve product name
            p = item.find("img").get("alt")
        except:
            p = None
        # Retrieve product link
        l = item.find('a').get('href')
        if "men" in l or "man" in l:
            # Store the name-link pair in category dictionary
            product_dic[str(p)]=l
    
    # Loop through each product in the dictionary
    for product, link in product_dic.items():
        
        # Store brand_name
        brand_name = "ecoalf"
        # Store scrapped_date
        scrapped_date = datetime.today().strftime('%Y-%m-%d')
        # Store gender
        gender = "Man"
        # Store secondhand
        secondhand = "No"
        
        # Run get_details function on each product page to retrieve details on each individual product
        product_material, color, image_link_color, size, price, description = get_details(link)
        
        # Append the new product to the products list
        products.append([product,product_material,color,size,price,link,image_link_color,brand_name,description,scrapped_date,category,gender,secondhand])
    
    return products
   

In [11]:
df_man = get_category(man)

In [ ]:
df_man

display_name  \
0                   Asp Jacket Man   
1                Armada Jacket Man   
2                 Beret Jacket Man   
3                  Baza Jacket Man   
4                 Cardiff Vest Man   
5               Ampuero Jacket Man   
6                Cartes Jacket Man   
7              Charco Raincoat Man   
8        Hampshire Long Jacket Man   
9               Livorno Jacket Man   
10              Iceberg Jacket Man   
11                Luena Jacket Man   
12           Lujar Long Jacket Man   
13               Katman Jacket Man   
14                Miera Jacket Man   
15   Vintage Reversible Jacket Man   
16   St Moritz Reversible Vest Man   
17                Breda Jacket Man   
18          Bareyo Long Jacket Man   
19               Bareyo Jacket Man   
20                 Pals Jacket Man   
21               Liendo Jacket Man   
22                Saro  Jacket Man   
23               Viccar Jacket Man   
24                Begur Jacket Man   
25               Bargas Jacket Man   
26                 Bayona Knit Man   
27             Illescas Jacket Man   
28              Sonseca Jacket Man   
29                   Vigo Knit Man   
30               Cadaques Knit Man   
31                Eduardo Knit Man   
32    Ecoalf Rubber Sweatshirt Man   
33          Bardero Sweatshirt Man   
34          Great B Sweatshirt Man   
35         Mandiore Sweatshirt Man   
36            Pardo Sweatshirt Man   
37        San Diego Sweatshirt Man   
38            Tisbu Sweatshirt Man   
39          Tribeca Sweatshirt Man   
40            Steve Sweatshirt Man   
41            Tutil Sweatshirt Man   
42             Ladd Sweatshirt Man   
43         Staunton Sweatshirt Man   
44            Yeles Sweatshirt Man   
45                Cardiff Vest Man   
46   St Moritz Reversible Vest Man   
47                Antejo Shirt Man   
48            Gotham Classic Shirt   
49      Garda Long Sleeve Polo Man   
50          Gotham Pique Shirt Man   
51           Andermatt T-Shirt Man   
52                Mino T-Shirt Man   
53        Andermatt Long Sleeve...   
54              Berdes T-Shirt Man   
55      Berdes Long Sleeve T-Shirt   
56             Great B T-Shirt Man   
57    Mino Long Sleeve T-Shirt Man   
58           New Natal Label Patch   
59               Nondo T-Shirt Man   
60  Patch Label Back Longsleeve...   
61               Rocas T-Shirt Man   
62             Tribeca T-Shirt Man   
63               Pardo T-Shirt Man   
64              Humber T-Shirt Man   
65                 Pablo Pants Man   
66                 Duero Pants Man   
67                Piedra Pants Man   
68           Yelo Cotton Pants Man   
69               Viccar Jacket Man   
70              Humber T-Shirt Man   
71                Saro  Jacket Man   
72                Eduardo Knit Man   
73            Valden Backpack  Man   
74                Piedra Pants Man   
75          Bareyo Long Jacket Man   
76               Bareyo Jacket Man   
77                Begur Jacket Man   
78               Liendo Jacket Man   
79                 Pals Jacket Man   
80               Cadaques Knit Man   
81             Ladd Sweatshirt Man   
82           Yelo Cotton Pants Man   
83          Gotham Pique Shirt Man   
84         Staunton Sweatshirt Man   
85            Yeles Sweatshirt Man   
86                      Samara Bag   
87               Jonic Slip On Man   
88              Jonic Sneakers Man   

                                     product_material  \
0                     {" Recycled polyester": "100%"}   
1   {" Recycled polyester": "59%", " Sorona\u00ae....   
2                     {" Recycled polyester": "100%"}   
3                     {" Recycled polyester": "100%"}   
4                     {" Recycled polyester": "100%"}   
5   {" Recycled polyester": "59%", " Sorona\u00ae....   
6   {" Recycled polyester": "59%", " Sorona\u00ae....   
7   {" Polyester": "56%", " Recycled polyester": "...   
8   {" Polyester": "56%", " Recycled polyester": "...   
9   {" Recycled polyester": "59

In [ ]:
# Kids' page

In [ ]:
kids = "https://ecoalf.com/en/kids-300"

In [ ]:
def get_product(category, category_link):
    page = BeautifulSoup(requests.get(category_link).content,'lxml')
    # Find all the div classes associated with a product
    product_class = page.find_all('div',class_="thumbnail-container")
    
    # Create an empty list to store products
    products = []
    
    # Create an empty category dictionary to store product name and link
    product_dic = {}
    for item in product_class:
        try:
            # Retrieve product name
            p = item.find("img").get("alt")
        except:
            p = None
        # Retrieve product link
        l = item.find('a').get('href')
        if "kids" in l:
            # Store the name-link pair in category dictionary
            product_dic[str(p)]=l
    
    # Loop through each product in the dictionary
    for product, link in product_dic.items():
        
        # Store brand_name
        brand_name = "ecoalf"
        # Store scrapped_date
        scrapped_date = datetime.today().strftime('%Y-%m-%d')
        # Store gender
        gender = "Kids"
        # Store secondhand
        secondhand = "No"
        
        # Run get_details function on each product page to retrieve details on each individual product
        product_material, color, image_link_color, size, price, description = get_details(link)
        
        # Append the new product to the products list
        products.append([product,product_material,color,size,price,link,image_link_color,brand_name,description,scrapped_date,category,gender,secondhand])
    
    return products
   

In [ ]:
df_kids = get_category(kids)

In [ ]:
df_kids

display_name  \
0                Asp Jacket Kids   
1              Marangu Coat Kids   
2                Gum Jacket Kids   
3                Kiko Vest  Kids   
4                Kim Jacket Kids   
5          Barca Sweatshirt Kids   
6           Celo Sweatshirt Kids   
7        Bardera Sweatshirt Kids   
8        Estuche Sweatshirt Kids   
9        Great B Sweatshirt Kids   
10       Pintura Sweatshirt Kids   
11         Lapiz Sweatshirt Kids   
12         Papel Sweatshirt Kids   
13    Multicolor Sweatshirt Kids   
14           Columpio Dress Kids   
15            Tobogan Dress Kids   
16                    Pants Kids   
17          Great B T-Shirt Kids   
18             Saca T-Shirt Kids   
19          Because T-Shirt Kids   
20          Borrada T-Shirt Kids   
21          Pizarra T-Shirt Kids   
22  Multi Because Long Sleeve...   
23      Rebel Multi T-Shirt Kids   
24             Rota T-Shirt Kids   
25           Columpio Dress Kids   
26            Tobogan Dress Kids   
27       Bardera Sweatshirt Kids   
28       Great B Sweatshirt Kids   
29       Pintura Sweatshirt Kids   
30          Great B T-Shirt Kids   
31          Because T-Shirt Kids   
32          Borrada T-Shirt Kids   
33  Multi Because Long Sleeve...   
34             Rota T-Shirt Kids   
35           Columpio Dress Kids   
36                    Pants Kids   

                                     product_material  \
0                     {" Recycled polyester": "100%"}   
1                     {" Recycled polyester": "100%"}   
2                     {" Recycled polyester": "100%"}   
3                     {" Recycled polyester": "100%"}   
4   {" Recycled polyester": "59%", " Sorona\u00ae....   
5   {" Recycled cotton": "50%", " Organic cotton":...   
6   {" Recycled cotton": "50%", " Organic cotton":...   
7   {" Recycled cotton": "50%", " Organic cotton":...   
8   {" Recycled cotton": "30%", " Organic cotton":...   
9   {" Organic cotton": "60%", " Recycled cotton":...   
10                                                 {}   
11  {" Recycled cotton": "50%", " Organic cotton":...   
12  {" Recycled cotton": "50%", " Organic cotton":...   
13  {" Recycled cotton": "50%", " Organic cotton":...   
14                                                 {}   
15  {" Recycled cotton": "50%", " Organic cotton":...   
16  {" Recycled cotton": "50%", " Organic cotton":...   
17  {" Recycled cotton": "50%", " Organic cotton":...   
18  {" Recycled cotton": "50%", " Organic cotton":...   
19  {" Recycled cotton": "50%", " Organic cotton":...   
20  {" Recycled cotton": "50%", " Organic cotton":...   
21  {" Recycled cotton": "50%", " Organic cotton":...   
22  {" Recycled cotton": "50%", " Organic cotton":...   
23  {" Recycled cotton": "50%", " Organic cotton":...   
24                                                 {}   
25                                                 {}   
26  {" Recycled cotton": "50%", " Organic cotton":...   
27  {" Recycled cotton": "50%", " Organic cotton":...   
28  {" Organic cotton": "60%", " Recycled cotton":...   
29                                                 {}   
30  {" Recycled cotton": "50%", " Organic cotton":...   
31  {" Recycled cotton": "50%", " Organic cotton":...   
32  {" Recycled cotton": "50%", " Organic cotton":...   
33  {" Recycled cotton": "50%", " Organic cotton":...   
34                                                 {}   
35                                                 {}   
36  {" Recycled cotton": "50%", " Organic cotton":...   

                                                color  \
0   ["lightmauve", "olive", "deepnavy", "shinyyell...   
1               ["lightmauve", "deepnavy", "asphalt"]   
2                               ["olive", "deepnavy"]   
3   ["lightmauve", "olive", "deepnavy", "shinyyell...   
4                               ["khaki", "deepnavy"]   
5                             ["lightpink", "caviar"]   
6                       ["washedblue", "navy", "red"]   
7                           

In [ ]:
# Woman shoes

In [ ]:
def get_shoes(url):
    lst = get_product_shoes("shoes",url)
        
    # Create dataframe
    df = pd.DataFrame(lst, columns =['display_name','product_material','color','size','price','product_url','image_link_color','brand_name','description','scrapped_date','low_level','gender','secondhand'])
    return df

In [ ]:
def get_product_shoes(category, category_link):
    page = BeautifulSoup(requests.get(category_link).content,'lxml')
    # Find all the div classes associated with a product
    product_class = page.find_all('div',class_="thumbnail-container")
    
    # Create an empty list to store products
    products = []
    
    # Create an empty category dictionary to store product name and link
    product_dic = {}
    for item in product_class:
        try:
            # Retrieve product name
            p = item.find("img").get("alt")
        except:
            p = None
        # Retrieve product link
        l = item.find('a').get('href')
        if "woman" in l or "man" in l:
            # Store the name-link pair in category dictionary
            product_dic[str(p)]=l
    
    # Loop through each product in the dictionary
    for product, link in product_dic.items():
        
        # Store brand_name
        brand_name = "ecoalf"
        # Store scrapped_date
        scrapped_date = datetime.today().strftime('%Y-%m-%d')
        # Store gender
        gender = "Woman"
        # Store secondhand
        secondhand = "No"
        
        # Run get_details function on each product page to retrieve details on each individual product
        product_material, color, image_link_color, size, price, description = get_details(link)
        
        # Append the new product to the products list
        products.append([product,product_material,color,size,price,link,image_link_color,brand_name,description,scrapped_date,category,gender,secondhand])
    
    return products
   

In [ ]:
woman_shoes = get_shoes("https://ecoalf.com/en/sneakers-180")

In [ ]:
woman_shoes

display_name  \
0            Prince Sneakers Woman   
1       Eliot Grape Sneakers Woman   
2             Riera Sneakers Woman   
3            Oregon Sneakers Woman   
4          Sandford Sneakers Woman   
5    Sandford Basic Sneakers Woman   
6             Patri Sneakers Woman   
7             Tenis Sneakers Woman   
8          Mulhacen Mid Boot Woman   
9                 Snow Boots Woman   
10        Snow Quilted Boots Woman   
11  Oregon Mid Boot Sneakers Woman   
12    Yale Mid Boot Sneakers Woman   
13          Pacific Mid Boot Woman   
14            Jonic Sneakers Woman   
15             Jonic Slip On Woman   

                                     product_material  \
0                         {" Recycled nylon": "100%"}   
1   {" Recycled polyester /31.7": "46.7%", " PU": ...   
2                         {" Recycled nylon": "100%"}   
3   {" Recycled polyester": "59%", " Sorona\u00ae....   
4                         {" Recycled nylon": "100%"}   
5                         {" Recycled nylon": "100%"}   
6   {" Recycled polyester": "59%", " Sorona\u00ae"...   
7                         {" Recycled nylon": "100%"}   
8    {" Recycled polyester": "50%", " Cotton": "50%"}   
9   {" Polyester": "56%", " Recycled polyester": "...   
10  {" Recycled polyester": "59%", " Sorona\u00ae....   
11  {" Recycled wool": "50%", " Recycled polyester...   
12                        {" Recycled nylon": "100%"}   
13  {" Recycled polyester": "59%", " Sorona\u00ae....   
14   {" Recycled polyester": "72%", " Cotton": "28%"}   
15  {" Recycled polyester /31.7": "46.7%", " PU": ...   

                                                color  \
0   ["offwhite", "fucsia", "burnedorange", "grape"...   
1                               ["offwhite", "black"]   
2                  ["white", "camel", "midnightnavy"]   
3            ["darksand", "silver", "khaki", "black"]   
4                   ["offwhite", "molegrey", "black"]   
5                                        ["offwhite"]   
6                                           ["black"]   
7                                        ["offwhite"]   
8                         ["linen", "brown", "black"]   
9                 ["darksand", "dustygreen", "black"]   
10                ["darksand", "dustygreen", "black"]   
11                       ["anthracite", "totalblack"]   
12                 ["darkkhaki", "deepnavy", "black"]   
13                                ["caviar", "black"]   
14                                          ["black"]   
15                                          ["black"]   

                                    size       price  \
0                                 ["36"]  USD 115.00   
1   ["36", "37", "38", "39", "40", "41"]  USD 175.00   
2   ["36", "37", "38", "39", "40", "41"]  USD 115.00   
3   ["36", "37", "38", "39", "40", "41"]  USD 115.00   
4   ["36", "37", "38", "39", "40", "41"]  USD 115.00   
5   ["36", "37", "38", "39", "40", "41"]  USD 115.00   
6         ["37", "38", "39", "40", "41"]  USD 185.00   
7   ["36", "37", "38", "39", "40", "41"]  USD 115.00   
8                                 ["41"]  USD 145.00   
9   ["36", "37", "38", "39", "40", "41"]  USD 175.00   
10  ["36", "37", "38", "39", "40", "41"]  USD 175.00   
11  ["36", "37", "38", "39", "40", "41"]  USD 145.00   
12  ["36", "37", "38", "39", "40", "41"]  USD 129.90   
13        ["36", "37", "38", "40", "41"]  USD 175.00   
14  ["36", "37", "38", "39", "40", "41"]  USD 185.00   
15  ["36", "37", "38", "39", "40", "41"]  USD 230.00   

                                          product_url  \
0   https://ecoalf.com/en/women/2120633-eliot-grap...   
1   https://ecoalf.com/en/women/2120596-oregon-sne...   
2   https://ecoalf.com/en/sneakers/2120638-mulhace...   
3   https://ecoalf.com/en/women/2120616-sandford-s...   
4   https://ecoalf.com/en/sneakers/2120651-prince-...   
5   https://ecoalf.com/en/sneakers/2120642-prince-...   
6   https://ecoalf.com/en/women/2120620-snow-sneak...   
7   https://ecoalf.com/en/

In [ ]:
# Man shoes

In [ ]:
def get_product_shoes(category, category_link):
    page = BeautifulSoup(requests.get(category_link).content,'lxml')
    # Find all the div classes associated with a product
    product_class = page.find_all('div',class_="thumbnail-container")
    
    # Create an empty list to store products
    products = []
    
    # Create an empty category dictionary to store product name and link
    product_dic = {}
    for item in product_class:
        try:
            # Retrieve product name
            p = item.find("img").get("alt")
        except:
            p = None
        # Retrieve product link
        l = item.find('a').get('href')
        if "woman" in l or "man" in l:
            # Store the name-link pair in category dictionary
            product_dic[str(p)]=l
    
    # Loop through each product in the dictionary
    for product, link in product_dic.items():
        
        # Store brand_name
        brand_name = "ecoalf"
        # Store scrapped_date
        scrapped_date = datetime.today().strftime('%Y-%m-%d')
        # Store gender
        gender = "Man"
        # Store secondhand
        secondhand = "No"
        
        # Run get_details function on each product page to retrieve details on each individual product
        product_material, color, image_link_color, size, price, description = get_details(link)
        
        # Append the new product to the products list
        products.append([product,product_material,color,size,price,link,image_link_color,brand_name,description,scrapped_date,category,gender,secondhand])
    
    return products
   

In [ ]:
man_shoes = get_shoes("https://ecoalf.com/en/sneakers-270")

In [ ]:
man_shoes

display_name  \
0            Prince Sneakers Man   
1       Eliot Grape Sneakers Man   
2           Caspian Sneakers Man   
3    Sandford Basic Sneakers Man   
4              Yale Sneakers Man   
5            Oregon Sneakers Man   
6             Riera Sneakers Man   
7          Sandford Sneakers Man   
8             Tenis Sneakers Man   
9          Beaufort Sneakers Man   
10           Cancun Sneakers Man   
11            Artic Sneakers Man   
12          Chronos Sneakers Man   
13  Oregon Mid Boot Sneakers Man   
14    Yale Mid Boot Sneakers Man   
15             Jonic Slip On Man   
16            Jonic Sneakers Man   

                                     product_material  \
0                         {" Recycled nylon": "100%"}   
1   {" Recycled polyester /31.7": "46.7%", " PU": ...   
2                         {" Recycled nylon": "100%"}   
3                         {" Recycled nylon": "100%"}   
4                         {" Recycled nylon": "100%"}   
5   {" Recycled polyester": "59%", " Sorona\u00ae....   
6                         {" Recycled nylon": "100%"}   
7                         {" Recycled nylon": "100%"}   
8                         {" Recycled nylon": "100%"}   
9   {" Recycled polyester": "59%", " Sorona\u00ae....   
10  {" Recycled polyester": "59%", " Sorona\u00ae....   
11  {" Recycled polyester": "59%", " Sorona\u00ae....   
12  {" Recycled polyester": "59%", " Sorona\u00ae....   
13  {" Recycled polyester": "59%", " Sorona\u00ae....   
14                        {" Recycled nylon": "100%"}   
15   {" Recycled polyester": "72%", " Cotton": "28%"}   
16   {" Recycled polyester": "72%", " Cotton": "28%"}   

                                                color  \
0   ["offwhite", "koreangreen", "deepnavy", "cavia...   
1                               ["offwhite", "black"]   
2                    ["steelblue", "caviar", "black"]   
3                               ["offwhite", "black"]   
4                ["koreangreen", "deepnavy", "black"]   
5   ["khaki", "midnightnavy", "caviar", "black", "...   
6                   ["offwhite", "deepnavy", "black"]   
7            ["offwhite", "deepnavy", "red", "black"]   
8                                  ["khaki", "black"]   
9                                           ["black"]   
10                                       ["deepnavy"]   
11                      ["darkkhaki", "midnightnavy"]   
12                                 ["khaki", "black"]   
13            ["khaki", "midnightnavy", "totalblack"]   
14                 ["darkkhaki", "deepnavy", "black"]   
15                                          ["black"]   
16                                          ["black"]   

                                          size       price  \
0                                       ["42"]  USD 115.00   
1         ["41", "42", "43", "44", "45", "46"]  USD 175.00   
2   ["40", "41", "42", "43", "44", "45", "46"]  USD 115.00   
3               ["42", "43", "44", "45", "46"]  USD 115.00   
4   ["40", "41", "42", "43", "44", "45", "46"]  USD 115.00   
5   ["40", "41", "42", "43", "44", "45", "46"]  USD 115.00   
6   ["40", "41", "42", "43", "44", "45", "46"]  USD 115.00   
7   ["40", "41", "42", "43", "44", "45", "46"]  USD 115.00   
8   ["40", "41", "42", "43", "44", "45", "46"]  USD 115.00   
9   ["40", "41", "42", "43", "44", "45", "46"]  USD 129.90   
10  ["40", "41", "42", "43", "44", "45", "46"]  USD 185.00   
11  ["40", "41", "42", "43", "44", "45", "46"]  USD 145.00   
12  ["40", "41", "42", "43", "44", "45", "46"]  USD 215.00   
13  ["40", "41", "42", "43", "44", "45", "46"]  USD 145.00   
14  ["40", "41", "42", "43", "44", "45", "46"]  USD 129.90   
15        ["40", "41", "42", "43", "44", "45"]  USD 230.00   
16        ["40", "41", "42", "43", "44", "45"]  USD 185.00   

                                          product_url  \
0   https://ecoalf.com/en/men/2120621-snow-sneaker...   
1   https://ecoalf.com/en/men/2120593-oregon-sneak...   
2   https://ecoalf.com/en/men

In [ ]:
# Kids shoes

In [ ]:
def get_product_shoes(category, category_link):
    page = BeautifulSoup(requests.get(category_link).content,'lxml')
    # Find all the div classes associated with a product
    product_class = page.find_all('div',class_="thumbnail-container")
    
    # Create an empty list to store products
    products = []
    
    # Create an empty category dictionary to store product name and link
    product_dic = {}
    for item in product_class:
        try:
            # Retrieve product name
            p = item.find("img").get("alt")
        except:
            p = None
        # Retrieve product link
        l = item.find('a').get('href')
        if "man" in l or "woman" in l:
            # Store the name-link pair in category dictionary
            product_dic[str(p)]=l
    
    # Loop through each product in the dictionary
    for product, link in product_dic.items():
        
        # Store brand_name
        brand_name = "ecoalf"
        # Store scrapped_date
        scrapped_date = datetime.today().strftime('%Y-%m-%d')
        # Store gender
        gender = "Kids"
        # Store secondhand
        secondhand = "No"
        
        # Run get_details function on each product page to retrieve details on each individual product
        product_material, color, image_link_color, size, price, description = get_details(link)
        
        # Append the new product to the products list
        products.append([product,product_material,color,size,price,link,image_link_color,brand_name,description,scrapped_date,category,gender,secondhand])
    
    return products
   

In [ ]:
kids_shoes = get_shoes("https://ecoalf.com/en/sneakers-505")

In [ ]:
kids_shoes

display_name             product_material  \
0       Sandford Sneakers Kids  {" Recycled nylon": "100%"}   
1  Yale Mid Boot Sneakers Kids  {" Recycled nylon": "100%"}   

                       color                                  size  \
0       ["offwhite", "pink"]  ["32", "33", "34", "35", "36", "37"]   
1  ["darkkhaki", "deepnavy"]  ["32", "33", "34", "35", "36", "37"]   

        price                                        product_url  \
0   USD 99.90  https://ecoalf.com/en/sneakers/2120644-prince-...   
1  USD 129.90  https://ecoalf.com/en/sneakers/2120662-yale-mi...   

                                    image_link_color brand_name  \
0  {"offwhite": "https://ecoalf.com/23679-thickbo...     ecoalf   
1  {"darkkhaki": "https://ecoalf.com/23673-thickb...     ecoalf   

                                         description scrapped_date low_level  \
0  The Sandford sports shoes are perfect for a ca...    2021-10-18     shoes   
1  The vintage-style Yale sneakers are the best e...    2021-10-18     shoes   

  gender secondhand  
0   Kids         No  
1   Kids         No

In [ ]:
# Combine three dfs to get a final df

In [ ]:
ecoalf_table = pd.concat([df_woman,df_man,df_kids,woman_shoes,man_shoes,kids_shoes],ignore_index = True)

In [ ]:
ecoalf_table

display_name  \
0                  Lenox Long Woman   
1                  Asp Jacket Woman   
2              Marangu Jacket Woman   
3              Amu New Jacket Woman   
4                Gedre Jacket Woman   
5              Glacier Jacket Woman   
6                Mandu Jacket Woman   
7                Marangu Vest Woman   
8             Mulhacen Woman Jacket   
9      Noir Reversible Jacket Woman   
10                 Uma Jacket Woman   
11     Sarrau Corduroy Jacket Woman   
12                 Tao Jacket Woman   
13             Ushuaia Jacket Woman   
14          New Croset Jacket Woman   
15    Vintage Diamonds Jacket Woman   
16             Esterri Jacket Woman   
17         Arties Vest Woman Jacket   
18                Snow Jacket Woman   
19               Tera Jacket  Woman   
20               Sagra Jacket Woman   
21              Mountain Woman Vest   
22                   Odra Top Woman   
23                Pino Jersey Woman   
24          Pino Round Woman Jersey   
25                Riaza Woman Dress   
26                 Val Sleeve Woman   
27     Vielha Turtle Seamless Woman   
28      Vielha Round Seamless Woman   
29            Tormes Woman Cardigan   
30               Cea Oversize Woman   
31                Inma Jersey Woman   
32               Tera Jacket  Woman   
33          Baiona Woman Sweatshirt   
34          Llanes Because Woman...   
35               Basic Woman Hoodie   
36                Aldan Woman Sweat   
37         Getaria Woman Sweatshirt   
38         Bolonia Woman Sweatshirt   
39       Cudillero Woman Sweatshirt   
40        Fornells Woman Sweatshirt   
41   Llanes Choice Woman Sweatshirt   
42            Lulu Woman Sweatshirt   
43      Acacia Woman Long Sleeve...   
44              Lavanda Shirt Woman   
45                 Wolf Shirt Woman   
46        Magnolia Long Shirt Woman   
47      Cortegana Woman Long Sleeve   
48            Because Woman T-Shirt   
49       Cadaques Woman Long Sleeve   
50            Mundaca Woman T-Shirt   
51    Choice Long Sleeve T-Shirt...   
52       Ecoalf Since Woman T-Shirt   
53            Great B Woman T-Shirt   
54                 Cega Pants Woman   
55             Penelope Woman Pants   
56                Nanga Pants Woman   
57                Patri Woman Pants   
58          Samani Pant-Skirt Woman   
59                Adaja Pants Woman   
60                 Arce Pants Woman   
61                Riaza Woman Dress   
62                 Noja Dress Woman   
63         Gabriel Long Dress Woman   
64                 Mery Woman Dress   
65          Nogal  Long Dress Woman   
66                Tahoe Dress Woman   
67            Olmo Belt Skirt Woman   
68                 Etna Skirt Woman   
69          Samani Pant-Skirt Woman   
70            Guadalupe Skirt Woman   
71                Mont  Dress Woman   
72                'BECAUSE' LEGGING   
73              Mountain Woman Vest   
74            Tormes Woman Cardigan   
75               Cea Oversize Woman   
76         Arties Vest Woman Jacket   
77            Olmo Belt Skirt Woman   
78                Inma Jersey Woman   
79                 Etna Skirt Woman   
80                Snow Jacket Woman   
81          Samani Pant-Skirt Woman   
82             Esterri Jacket Woman   
83                Adaja Pants Woman   
84              Jonic Slip On Woman   
85             Jonic Sneakers Woman   
86                 Wolf Shirt Woman   
87               Tera Jacket  Woman   
88                Mont  Dress Woman   
89            Guadalupe Skirt Woman   
90        Magnolia Long Shirt Woman   
91               Sagra Jacket Woman   
92                 Arce Pants Woman   
93   Spoo Medium Size Shopper Woman   
94                       Samara Bag   
95      Spoo Big Size Shopper Woman   
96         Getaria Woman Sweatshirt   
97          Llanes Because Woman...   
98            Because Woman T-Shirt   
99    Choice Long Sleeve T-Shirt...   
100           Great B Woman T-Shirt   
101                  Asp Jacket Man   
102   

In [ ]:
# Save df to csv
ecoalf_table.to_csv('ecoalf_table.csv')

In [ ]:
# Cleaning and combining data from all brands

In [ ]:
pip install psycopg2-binary

     |████████████████████████████████| 2.1 MB 7.9 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [ ]:
import psycopg2
import pandas as pd
import numpy as np
import re
import datetime as dt

In [ ]:
df = pd.read_csv('ecoalf_table.csv')

In [ ]:
GranCat = pd.read_csv("LowLevelCatagoryRegex.csv", header=None, skiprows=[0])

def process_cat(df):
    # get all the values in category regex
    subCats = GranCat.iloc[:, 1:]
    Cats = []
    for index, row in subCats.iterrows():
        for i in GranCat.columns[1:]:
            if pd.isnull(row[i]): continue
            else: Cats.append(row[i])
               
    # assign potential category for each clothing row based on title, else other
    clothesCat = []
    for index, row in df.iterrows():
        rowCat = float("NaN")
        for cat in Cats:
            if re.search(cat, row['display_name'].lower()):
                rowCat = cat
                print(rowCat)
                break
        if pd.isnull(rowCat):
            clothesCat.append('other')
        else:
            clothesCat.append(rowCat)

    return clothesCat

# set parent category to each product
def get_cat(x):
    if x == 'other': return x
    else: return [GranCat[0][i] for i in GranCat.index if x in GranCat.iloc[i].to_list()][0]

# get low_level column given a df
def get_lowlevel(df):
    df['low_level_new'] = process_cat(df)
    df['low_level_new'] = df['low_level_new'].apply(lambda x: get_cat(x))
    return df

In [ ]:
def get_id(df, date='20211025'):
    brand = df['brand_name'][0]
    clothing_ids = []
    for i in range(len(df.index)):
        clothing_id = date + brand + str(i)
        clothing_ids.append(clothing_id)
    return clothing_ids

In [ ]:
df = pd.read_csv('ecoalf_table.csv')

In [ ]:
df = get_lowlevel(df)

jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
vest
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
vest$
tops?
dresse?s?$
cardigan
jackets?
sweatshirts?
hoodies?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
shirts?
shirts?
shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
pants?
pants?
pants?
pants?
sk[io]rts?
pants?
pants?
dresse?s?$
dresse?s?
dresse?s?
dresse?s?$
dresse?s?
dresse?s?
sk[io]rts?
sk[io]rts?
sk[io]rts?
sk[io]rts?
dresse?s?
[jl]eggings?
vest$
cardigan
jackets?
sk[io]rts?
sk[io]rts?
jackets?
sk[io]rts?
jackets?
pants?
sneakers?
shirts?
jackets?
dresse?s?
sk[io]rts?
shirts?
jackets?
pants?
bags?
sweatshirts?
t-?shirts?
t-?shirts?
t-?shirts?
jackets?
jackets?
jackets?
jackets?
cardi
jackets?
jackets?
coats?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
vest
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?
jackets?


In [ ]:
df[['display_name','low_level_new']]

display_name low_level_new
0               Lenox Long Woman         other
1               Asp Jacket Woman       Jackets
2           Marangu Jacket Woman       Jackets
3           Amu New Jacket Woman       Jackets
4             Gedre Jacket Woman       Jackets
..                           ...           ...
257   Yale Mid Boot Sneakers Man      Sneakers
258            Jonic Slip On Man         other
259           Jonic Sneakers Man      Sneakers
260       Sandford Sneakers Kids      Sneakers
261  Yale Mid Boot Sneakers Kids      Sneakers

[262 rows x 2 columns]

In [ ]:
df[df['low_level_new']=='other'][['display_name','low_level_new']]

display_name low_level_new
0                  Lenox Long Woman         other
23                Pino Jersey Woman         other
24          Pino Round Woman Jersey         other
26                 Val Sleeve Woman         other
27     Vielha Turtle Seamless Woman         other
28      Vielha Round Seamless Woman         other
30               Cea Oversize Woman         other
31                Inma Jersey Woman         other
34          Llanes Because Woman...         other
36                Aldan Woman Sweat         other
43      Acacia Woman Long Sleeve...         other
47      Cortegana Woman Long Sleeve         other
49       Cadaques Woman Long Sleeve         other
75               Cea Oversize Woman         other
78                Inma Jersey Woman         other
84              Jonic Slip On Woman         other
93   Spoo Medium Size Shopper Woman         other
95      Spoo Big Size Shopper Woman         other
97          Llanes Because Woman...         other
154        Andermatt Long Sleeve...         other
159           New Natal Label Patch         other
161  Patch Label Back Longsleeve...         other
188               Jonic Slip On Man         other
212    Multi Because Long Sleeve...         other
223    Multi Because Long Sleeve...         other
242             Jonic Slip On Woman         other
258               Jonic Slip On Man         other

In [ ]:
df=df.drop(['low_level'], axis=1)

In [ ]:
df = df.rename(columns={"low_level_new": "low_level"})

In [ ]:
df['clothing_id'] = get_id(df)

In [ ]:
df = df.set_index('clothing_id')

In [ ]:
df=df.drop(['Unnamed: 0'], axis=1)

In [ ]:
df_ecoalf = df

In [ ]:
df_ecoalf.to_csv('ecoalf_table.csv')

In [ ]:
# Cleaning low_level for OrganicBasic

In [ ]:
df = pd.read_csv('OB+NJ_Combined_clean.csv')

In [ ]:
df = df.set_index('clothing_id')

In [ ]:
df = df.rename(columns={"materials": "product_material"})

In [ ]:
df

display_name  \
clothing_id                                                                   
20211017organicbasics1                           TENCEL� Lite Boxers 2-Pack   
20211017organicbasics2                         Organic Cotton Boxers 2-pack   
20211017organicbasics3                                   Organic Cotton Tee   
20211017organicbasics4                      Organic Cotton Mid-Weight Sweat   
20211017organicbasics5                         Organic Cotton Briefs 2-pack   
20211017organicbasics6                          Organic Cotton Triangle Bra   
20211017organicbasics7                           Organic Cotton Stretch Tee   
20211017organicbasics8                            Organic Cotton Turtleneck   
20211017organicbasics9                               SilverTech� Active Tee   
20211017organicbasics10                             TENCEL� Lite Long Johns   
20211017organicbasics11                               TENCEL� Lite Bralette   
20211017organicbasics12                     SilverTech� Active Tennis Socks   
20211017organicbasics13                                     Active Leggings   
20211017organicbasics15                          Organic Cotton Classic Bra   
20211017organicbasics16                                  Organic Cotton Tee   
20211017organicbasics17                    Organic Cotton Rib-Flex Tank Bra   
20211017organicbasics18                         Organic Cotton Rib-Flex Tee   
20211017organicbasics19   Organic Cotton Rib-Flex Super High-Rise Briefs...   
20211017organicbasics20                              Re-Swim Bikini Bottoms   
20211017organicbasics21                                   Re-Swim One-Piece   
20211017organicbasics22                                  Re-Swim Bikini Top   
20211017organicbasics23                                       Invisible Bra   
20211017organicbasics24                         TENCEL� Lite Basic Bralette   
20211017organicbasics25                                  Active Bike Shorts   
20211017organicbasics26                            Organic Cotton Basic Bra   
20211017organicbasics27                       Organic Cotton Hipster 2-pack   
20211017organicbasics28                         Organic Cotton Thong 2-pack   
20211017organicbasics29        Organic Cotton Super High-Rise Briefs 2-pack   
20211017organicbasics30                                  Active Workout Bra   
20211017organicbasics31                                   Active Sports Bra   
20211017organicbasics32                                 Active 3/4 Leggings   
20211017organicbasics33                       TENCEL� Woven Draw-Cord Pants   
20211017organicbasics34             Organic Cotton Mid-Weight Cropped Sweat   
20211017organicbasics35                Organic Cotton Mid-Weight Sweatpants   
20211017organicbasics36                                        Active Thong   
20211017organicbasics37                   Re-Tights High-Rise 80 Den 2-pack   
20211017organicbasics38                Organic Cotton Mid-Weight Sweat-Hood   
20211017organicbasics39                   Re-Tights High-Rise 20 Den 2-pack   
20211017organicbasics40                                      Active Hipster   
20211017organicbasics41                     Organic Cotton Heavy Sweat-Hood   
20211017organicbasics42                  Organic Cotton Heavy Cropped Sweat   
20211017organicbasics43                             Recycled Wool Boxy Knit   
20211017organicbasics44                    Organic Cotton Oxford Long Shirt   
20211017organicbasics45                                    TENCEL� Lite Tee   
20211017organicbasics46                                 TENCEL� Lite Shorts   
20211017organicbasics47                           TENCEL� Lite Tanga 2-pack   
20211017organicbasics48                          TENCEL� Lite Shorty 2-pack   
20211017organicbasics49                      Invisible Cheeky Briefs 2-pack   
20211017organicbasics50                       Invisible Cheeky Thong 2-pack   
20211017organicbasics51           

In [ ]:
df=df.drop(['materials1'], axis=1)

In [ ]:
df['scrapped_date']='10/18/21'

In [ ]:
df_ob_nj = df

In [ ]:
df_kto = pd.read_csv('KnowtheOrigin_table.csv')

In [ ]:
df_kto = df_kto.set_index('clothing_id')

In [ ]:
df_kto = df_kto.rename(columns={"image_color_link": "image_link_color"})

In [ ]:
df_kto

display_name  \
clothing_id                                                                  
20211021KnowtheOrigin0                       Topanga Recycled PET Bra Plum   
20211021KnowtheOrigin1               Flora Organic Cotton Check Dress Navy   
20211021KnowtheOrigin2         Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin3     Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin4               Handy 100% Recycled PET Backpack Rust   
...                                                                    ...   
20211021KnowtheOrigin250                            Space Socks Denim Blue   
20211021KnowtheOrigin251  Organic Cotton Short Sleeved T-Shirt Washed Grey   
20211021KnowtheOrigin252                           Recycled Denim Tote Bag   
20211021KnowtheOrigin253                     Hajo Mini Lotus Backpack Nude   
20211021KnowtheOrigin254           Hajo Mini  Lotus Backpack Honey Mustard   

                                                                product_url  \
clothing_id                                                                   
20211021KnowtheOrigin0    https://knowtheorigin.com/products/copy-of-top...   
20211021KnowtheOrigin1    https://knowtheorigin.com/products/flora-check...   
20211021KnowtheOrigin2    https://knowtheorigin.com/products/copy-of-mod...   
20211021KnowtheOrigin3    https://knowtheorigin.com/products/modelo-89-r...   
20211021KnowtheOrigin4    https://knowtheorigin.com/products/handy-100-r...   
...                                                                     ...   
20211021KnowtheOrigin250  https://knowtheorigin.com/products/space-socks...   
20211021KnowtheOrigin251  https://knowtheorigin.com/products/grey-washed...   
20211021KnowtheOrigin252  https://knowtheorigin.com/products/wawwa-recyc...   
20211021KnowtheOrigin253  https://knowtheorigin.com/products/hajo-mini-n...   
20211021KnowtheOrigin254  https://knowtheorigin.com/products/hajo-mini-h...   

                                price  \
clothing_id                             
20211021KnowtheOrigin0         $48.99   
20211021KnowtheOrigin1        $130.99   
20211021KnowtheOrigin2        $171.99   
20211021KnowtheOrigin3        $171.99   
20211021KnowtheOrigin4         $61.99   
...                               ...   
20211021KnowtheOrigin250  $6.99,$9.99   
20211021KnowtheOrigin251       $38.99   
20211021KnowtheOrigin252       $48.99   
20211021KnowtheOrigin253      $103.99   
20211021KnowtheOrigin254      $103.99   

                                                                       size  \
clothing_id                                                                   
20211021KnowtheOrigin0    ["XXS", "XS", "S", "M", "L", "XL", "XXL", "XXX...   
20211021KnowtheOrigin1                          ["XS", "S", "M", "L", "XL"]   
20211021KnowtheOrigin2    ["36", "37", "38", "39", "40", "41", "42", "43...   
20211021KnowtheOrigin3    ["36", "37", "38", "39", "40", "41", "42", "43...   
20211021KnowtheOrigin4                                                   []   
...                                                                     ...   
20211021KnowtheOrigin250                                           ["7-11"]   
20211021KnowtheOrigin251                              ["S", "M", "L", "XL"]   
20211021KnowtheOrigin252                                                 []   
20211021KnowtheOrigin253                                                 []   
20211021KnowtheOrigin254                                                 []   

                                                                description  \
clothing_id                                                                   
20211021KnowtheOrigin0    The high-neck cross-back sports bra, produced ...   
20211021KnowtheOrigin1    Loose fit navy turtleneck dress in check print...   
20211021KnowtheOrigin2    The Model 89 is the signature style from 80s i...   
20211021KnowtheOrigin3    The Model 89 is the signature style 

In [ ]:
df = pd.read_csv('ABCH_fordays.csv')

In [ ]:
df

Unnamed: 0             display_name     product_material  \
0             0             T-shirtDress  {'Cotton': '100% '}   
1             1    SleevelessSkivvyDress  {'Cotton': '100% '}   
2             2    LongSleeveSkivvyDress  {'Cotton': '100% '}   
3             3          ShortLinenDress    {'Linen': '100%'}   
4             4        TencelLoungeDress    {'Linen': '100%'}   
..          ...                      ...                  ...   
280         103            LogoOOOJogger   {'Cotton': '100%'}   
281         104           CoolDaysJogger   {'Cotton': '100%'}   
282         105              40'sHalfZip   {'Cotton': '100%'}   
283         106     Re-FreshFleeceJogger   {'Cotton': '100%'}   
284         107  Re-FreshFleeceZipHoodie   {'Cotton': '100%'}   

                                                 color  \
0                                            ['Black']   
1                                            ['Black']   
2                                            ['Black']   
3                                            ['Black']   
4                                            ['Black']   
..                                                 ...   
280  ['LG3501W-BLACK-l', 'LG3501W-SAGE-l', 'WSizeCh...   
281  ['150014W-DARKGREEN-l', '150014W-BLACK-l', '15...   
282  ['S03201W-BLACK-l', 'S03201W-CREAM-l', 'WSizeC...   
283  ['350004U_CINNAMON_', '350004U_NAVY_', '350004...   
284  ['330005U_CINNAMON_', '330005U_CHARCOAL_', '33...   

                                                  size      price  \
0       ['XXS', 'XS', 'S', 'M', 'L', 'XL', 'XXL', 'C']     USD 90   
1       ['XXS', 'XS', 'S', 'M', 'L', 'XL', 'XXL', 'C']    USD 145   
2       ['XXS', 'XS', 'S', 'M', 'L', 'XL', 'XXL', 'C']    USD 150   
3                     ['XS', 'S', 'M', 'L', 'XL', 'C']    USD 295   
4                     ['XS', 'S', 'M', 'L', 'XL', 'C']    USD 355   
..                                                 ...        ...   
280  ['\n            SAGE\n          ', 'XS', 'S', ...  USD 54.00   
281  ['\n            ECRU\n          ', '\n        ...  USD 54.00   
282  ['\n            BLACK\n          ', 'XS', 'S',...  USD 52.00   
283  ['\n            NAVY\n          ', '\n        ...  USD 66.00   
284  ['\n            CHARCOAL\n          ', '\n    ...  USD 68.00   

                                           product_url  \
0    https://abch.world/collections/womens/products...   
1    https://abch.world/collections/womens/products...   
2    https://abch.world/collections/womens/products...   
3    https://abch.world/collections/womens/products...   
4    https://abch.world/collections/womens/products...   
..                                                 ...   
280  https://fordays.com/collections/women-sweats/p...   
281  https://fordays.com/collections/women-sweats/p...   
282  https://fordays.com/collections/women-sweats/p...   
283  https://fordays.com/collections/women-sweats/p...   
284  https://fordays.com/collections/women-sweats/p...   

                                      image_link_color brand_name  \
0    {'Black': '//cdn.shopify.com/s/files/1/1637/85...      A.BCH   
1    {'Black': '//cdn.shopify.com/s/files/1/1637/85...      A.BCH   
2    {'Black': '//cdn.shopify.com/s/files/1/1637/85...      A.BCH   
3    {'Black': '//cdn.shopify.com/s/files/1/1637/85...      A.BCH   
4    {'Black': '//cdn.shopify.com/s/files/1/1637/85...      A.BCH   
..                                                 ...        ...   
280  {'LG3501W-BLACK-l': '//cdn.shopify.com/s/files...    fordays   
281  {'150014W-DARKGREEN-l': '//cdn.shopify.com/s/f...    fordays   
282  {'S03201W-BLACK-l': '//cdn.shopify.com/s/files...    fordays   
283  {'350004U_CINNAMON_': '//cdn.shopify.com/s/fil...    fordays   
284  {'330005U_CINNAMON_': '//cdn.shopify.com/s/fil...    fordays   

                                           description scrapped_date  \
0    T-shirt dresses are a tricky thing to master, ...       27:26.6   
1    The oh-so-elegant A.14 

In [ ]:
df = get_lowlevel(df)

dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
dresse?s?$
coats?
jackets?
sweaters?
sweaters?
sweaters?
sk[io]rts?
sk[io]rts?
sk[io]rts?
sk[io]rts?
skivvy
dresse?s?$
dresse?s?$
shorts
sleeveless
skivvy
dresse?s?$
dresse?s?$
sleeveless
shorts
shorts
sleeveless
dresse?s?$
dresse?s?$
skivvy
dresse?s?$
skivvy
shorts
dresse?s?$
sleeveless
skivvy
shorts
dresse?s?$
sleeveless
dresse?s?$
skivvy
shorts
sleeveless
dresse?s?$
dresse?s?$
dresse?s?$
sweaters?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
sweaters?
sweaters?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
sweaters?
sweaters?
t-?shirts?
t-?shirts?
dresse?s?$
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
sweaters?
dresse?s?$
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shir

In [ ]:
df[['display_name','low_level_new']]

display_name low_level_new
0               T-shirtDress  Midi Dresses
1      SleevelessSkivvyDress  Midi Dresses
2      LongSleeveSkivvyDress  Midi Dresses
3            ShortLinenDress  Midi Dresses
4          TencelLoungeDress  Midi Dresses
..                       ...           ...
280            LogoOOOJogger       Joggers
281           CoolDaysJogger       Joggers
282              40'sHalfZip         other
283     Re-FreshFleeceJogger       Joggers
284  Re-FreshFleeceZipHoodie       Hoodies

[285 rows x 2 columns]

In [ ]:
len(df[df['low_level_new']=='other'][['display_name','low_level_new']])

40

In [ ]:
df = df.drop(['low_level'], axis=1)

In [ ]:
df = df.rename(columns={"low_level_new": "low_level"})

In [ ]:
df['clothing_id'] = get_id(df)

In [ ]:
df = df.set_index('clothing_id')

In [ ]:
df

display_name     product_material  \
clothing_id                                                      
20211025A.BCH0               T-shirtDress  {'Cotton': '100% '}   
20211025A.BCH1      SleevelessSkivvyDress  {'Cotton': '100% '}   
20211025A.BCH2      LongSleeveSkivvyDress  {'Cotton': '100% '}   
20211025A.BCH3            ShortLinenDress    {'Linen': '100%'}   
20211025A.BCH4          TencelLoungeDress    {'Linen': '100%'}   
...                                   ...                  ...   
20211025A.BCH280            LogoOOOJogger   {'Cotton': '100%'}   
20211025A.BCH281           CoolDaysJogger   {'Cotton': '100%'}   
20211025A.BCH282              40'sHalfZip   {'Cotton': '100%'}   
20211025A.BCH283     Re-FreshFleeceJogger   {'Cotton': '100%'}   
20211025A.BCH284  Re-FreshFleeceZipHoodie   {'Cotton': '100%'}   

                                                              color  \
clothing_id                                                           
20211025A.BCH0                                            ['Black']   
20211025A.BCH1                                            ['Black']   
20211025A.BCH2                                            ['Black']   
20211025A.BCH3                                            ['Black']   
20211025A.BCH4                                            ['Black']   
...                                                             ...   
20211025A.BCH280  ['LG3501W-BLACK-l', 'LG3501W-SAGE-l', 'WSizeCh...   
20211025A.BCH281  ['150014W-DARKGREEN-l', '150014W-BLACK-l', '15...   
20211025A.BCH282  ['S03201W-BLACK-l', 'S03201W-CREAM-l', 'WSizeC...   
20211025A.BCH283  ['350004U_CINNAMON_', '350004U_NAVY_', '350004...   
20211025A.BCH284  ['330005U_CINNAMON_', '330005U_CHARCOAL_', '33...   

                                                               size  \
clothing_id                                                           
20211025A.BCH0       ['XXS', 'XS', 'S', 'M', 'L', 'XL', 'XXL', 'C']   
20211025A.BCH1       ['XXS', 'XS', 'S', 'M', 'L', 'XL', 'XXL', 'C']   
20211025A.BCH2       ['XXS', 'XS', 'S', 'M', 'L', 'XL', 'XXL', 'C']   
20211025A.BCH3                     ['XS', 'S', 'M', 'L', 'XL', 'C']   
20211025A.BCH4                     ['XS', 'S', 'M', 'L', 'XL', 'C']   
...                                                             ...   
20211025A.BCH280  ['\n            SAGE\n          ', 'XS', 'S', ...   
20211025A.BCH281  ['\n            ECRU\n          ', '\n        ...   
20211025A.BCH282  ['\n            BLACK\n          ', 'XS', 'S',...   
20211025A.BCH283  ['\n            NAVY\n          ', '\n        ...   
20211025A.BCH284  ['\n            CHARCOAL\n          ', '\n    ...   

                      price  \
clothing_id                   
20211025A.BCH0       USD 90   
20211025A.BCH1      USD 145   
20211025A.BCH2      USD 150   
20211025A.BCH3      USD 295   
20211025A.BCH4      USD 355   
...                     ...   
20211025A.BCH280  USD 54.00   
20211025A.BCH281  USD 54.00   
20211025A.BCH282  USD 52.00   
20211025A.BCH283  USD 66.00   
20211025A.BCH284  USD 68.00   

                                                        product_url  \
clothing_id                                                           
20211025A.BCH0    https://abch.world/collections/womens/products...   
20211025A.BCH1    https://abch.world/collections/womens/products...   
20211025A.BCH2    https://abch.world/collections/womens/products...   
20211025A.BCH3    https://abch.world/collections/womens/products...   
20211025A.BCH4    https://abch.world/collections/womens/products...   
...                                                             ...   
20211025A.BCH280  https://fordays.com/collections/women-sweats/p...   
20211025A.BCH281  https://fordays.com/collections/women-sweats/p...   
20211025A.BCH282  https://fordays.com/collections/women-sweats/p...   
20211025A.BCH283  https://fordays.com/collections/women-sweats/p...   
20211025A.BCH284  https://fordays.com/collections/women-sweats/p..

In [ ]:
df=df.drop(['Unnamed: 0'], axis=1)

In [ ]:
df_abch_fd = df

In [ ]:
df = pd.read_csv('pangaia_table 2.csv')

In [ ]:
df = get_lowlevel(df)

sk[io]rts?
sk[io]rts?
sk[io]rts?
tank
tank
tank
hoodies?
hoodies?
hoodies?
hoodies?
pants?
pants?
pants?
pants?
shorts
shorts
shorts
shorts
shorts
shorts
shorts
shorts
shorts
shorts
shorts
shorts
shorts
t-?shirts?
pants?
t-?shirts?
pants?
hoodies?
hoodies?
shorts
hoodies?
hoodies?
sweatshirts?
hoodies?
sweatshirts?
sweatshirts?
shorts
shorts
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
t-?shirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
sweatshirts?
t-?shirts?
t-?shirts?
t-?shirts?
hoodies?
shorts
shorts
shorts
shorts
shorts
shorts
sweatshirts?
shorts
caps?
cuff
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
hats?
hats?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
cuff
cuff
beanies?
cuff
beanies?
cuff
cuff
cuff
bombers?
sweatshirts?
sweatshirts?
bombers?
hoodies?
bombers?
pants?
pant

In [ ]:
df[df['low_level_new']=='other'][['display_name','low_level_new']]

display_name low_level_new
0                          5 Tree Credits—the seedling         other
1                         10 Tree Credits—the woodland         other
2                           15 Tree Credits—the forest         other
30                                Pangaia E-Gift Card—         other
31                        50 Tree Credits—mother earth         other
201            Recycled Cashmere Set—pale grey melange         other
202                Recycled Cashmere Set—orchid purple         other
203                      Recycled Cashmere Set—oatmeal         other
204                        Recycled Cashmere Set—camel         other
205                     Recycled Cashmere Set—burgundy         other
206                    Recycled Cashmere Set—blue teal         other
207                        Recycled Cashmere Set—black         other
328                       Offset Your Summer Road Trip         other
329               Offset Your Short-Haul Return Flight         other
330                                  Offset Your Phone         other
331                Offset Your Long-Haul Return Flight         other
332                     Offset Your Driving For A Year         other
486                          Jersey Hood—orchid purple         other
487                            Jersey Hood—cobalt blue         other
488                                  Jersey Hood—black         other
613  Support Marine Life Research with Michael In K...         other
614           Support Bee Research with Mats In Sweden         other
617   Protect Sea Turtles with Christine In Costa Rica         other
618              Protect Jaguars with José In Colombia         other
713  Help Francois Rescue Trafficked Pangolins In S...         other
714             Help Dino Conserve Bees In East Africa         other
715         Build B-Lines For Bees with Paul In The Uk         other
798                  Pangaia X Air-Ink® Hood—off-white         other

In [ ]:
df = df.drop(['low_level'], axis=1)

In [ ]:
df = df.rename(columns={"low_level_new": "low_level"})

In [ ]:
df['clothing_id'] = get_id(df)

In [ ]:
df = df.set_index('clothing_id')

In [ ]:
df_pan = df

In [ ]:
df = pd.read_csv('eileenfisher_table.csv')

In [ ]:
df['clothing_id'] = get_id(df)

In [ ]:
df = df.set_index('clothing_id')

In [ ]:
df_ef = df

In [ ]:
df_pan = df_pan.drop(['clothing_id'], axis=1)

In [ ]:
df_pan

display_name  \
clothing_id                                                             
20211025PANGAIA0                          5 Tree Credits—the seedling   
20211025PANGAIA1                         10 Tree Credits—the woodland   
20211025PANGAIA2                           15 Tree Credits—the forest   
20211025PANGAIA3    Women's Summer Towelling Wrap Skirt—orchid purple   
20211025PANGAIA4    Women's Summer Towelling Wrap Skirt—flamingo pink   
20211025PANGAIA5            Women's Summer Towelling Wrap Skirt—black   
20211025PANGAIA6      Women's Summer Towelling Tank Top—flamingo pink   
20211025PANGAIA7        Women's Summer Towelling Tank Top—cobalt blue   
20211025PANGAIA8              Women's Summer Towelling Tank Top—black   
20211025PANGAIA9       Women's Summer Towelling Slim Fit Hoodie—stone   
20211025PANGAIA10   Women's Summer Towelling Slim Fit Hoodie—flami...   
20211025PANGAIA11   Women's Summer Towelling Slim Fit Hoodie—cobal...   
20211025PANGAIA12      Women's Summer Towelling Slim Fit Hoodie—black   
20211025PANGAIA13          Women's Recycled Cashmere Track Pants—sand   
20211025PANGAIA14     Women's Recycled Cashmere Track Pants—rose pink   
20211025PANGAIA15   Women's Recycled Cashmere Track Pants—dark for...   
20211025PANGAIA16         Women's Recycled Cashmere Track Pants—cream   
20211025PANGAIA17                      Kids 365 Shorts—celestial blue   
20211025PANGAIA18                         Kids 365 Shorts—cobalt blue   
20211025PANGAIA19                       Kids 365 Shorts—flamingo pink   
20211025PANGAIA20                          Kids 365 Shorts—jade green   
20211025PANGAIA21                       Kids 365 Shorts—orchid purple   
20211025PANGAIA22                    Kids 365 Shorts—persimmon orange   
20211025PANGAIA23                      Kids 365 Shorts—saffron yellow   
20211025PANGAIA24                               Kids 365 Shorts—stone   
20211025PANGAIA25                           Kids 365 Shorts—off-white   
20211025PANGAIA26                               Kids 365 Shorts—black   
20211025PANGAIA27                                Kids 365 Shorts—sand   
20211025PANGAIA28                                Kids 365 Shorts—grey   
20211025PANGAIA29                          Kids 365 Long Shorts—stone   
20211025PANGAIA30                                Pangaia E-Gift Card—   
20211025PANGAIA31                        50 Tree Credits—mother earth   
20211025PANGAIA32        PPRMINT™ Organic Cotton T-shirt—purple coral   
20211025PANGAIA33   Women's Recycled Cashmere Track Pants—cornflow...   
20211025PANGAIA34       Organic Cotton Long Sleeve T-shirt—jade green   
20211025PANGAIA35     Women's Recycled Cashmere Track Pants—coral red   
20211025PANGAIA36              Women's Recycled Cashmere Hoodie—cream   
20211025PANGAIA37    Women's Recycled Cashmere Hoodie—cornflower blue   
20211025PANGAIA38     Lightweight Recycled Cotton Shorts—purple coral   
20211025PANGAIA39        Women's Recycled Cashmere Hoodie—cobalt blue   
20211025PANGAIA40              Women's Recycled Cashmere Hoodie—black   
20211025PANGAIA41       Women's PPRMINT™ Half Zip Sweatshirt—burgundy   
20211025PANGAIA42   Women's Lightweight Recycled Cotton Fitted Zip...   
20211025PANGAIA43                 Women's Funnel Neck Sweatshirt—sand   
20211025PANGAIA44       Women's Funnel Neck Sweatshirt—rosemary green   
20211025PANGAIA45      Lightweight Recycled Cotton Shorts—mineral red   
20211025PANGAIA46      Lightweight Recycled Cotton Shorts—plum purple   
20211025PANGAIA47        Women's Funnel Neck Sweatshirt—orchid purple   
20211025PANGAIA48                  Kids 365 Sweatshirt—celestial blue   
20211025PANGAIA49                     Kids 365 Sweatshirt—cobalt blue   
20211025PANGAIA50                   Kids 365 Sweatshirt—flamingo pink   
20211025PANGAIA51                      Kids 365 Sweatshirt—jade green   
20211025PANGAIA52                   Kids 365 Sweatshirt—orchid purple   
20211025PANGAIA53                Kids 365 

In [ ]:
combined_table = pd.concat([df_ecoalf,df_ob_nj,df_kto,df_abch_fd,df_pan,df_ef])

In [ ]:
combined_table

display_name  \
clothing_id                                                                   
20211025ecoalf0                                            Lenox Long Woman   
20211025ecoalf1                                            Asp Jacket Woman   
20211025ecoalf2                                        Marangu Jacket Woman   
20211025ecoalf3                                        Amu New Jacket Woman   
20211025ecoalf4                                          Gedre Jacket Woman   
20211025ecoalf5                                        Glacier Jacket Woman   
20211025ecoalf6                                          Mandu Jacket Woman   
20211025ecoalf7                                          Marangu Vest Woman   
20211025ecoalf8                                       Mulhacen Woman Jacket   
20211025ecoalf9                                Noir Reversible Jacket Woman   
20211025ecoalf10                                           Uma Jacket Woman   
20211025ecoalf11                               Sarrau Corduroy Jacket Woman   
20211025ecoalf12                                           Tao Jacket Woman   
20211025ecoalf13                                       Ushuaia Jacket Woman   
20211025ecoalf14                                    New Croset Jacket Woman   
20211025ecoalf15                              Vintage Diamonds Jacket Woman   
20211025ecoalf16                                       Esterri Jacket Woman   
20211025ecoalf17                                   Arties Vest Woman Jacket   
20211025ecoalf18                                          Snow Jacket Woman   
20211025ecoalf19                                         Tera Jacket  Woman   
20211025ecoalf20                                         Sagra Jacket Woman   
20211025ecoalf21                                        Mountain Woman Vest   
20211025ecoalf22                                             Odra Top Woman   
20211025ecoalf23                                          Pino Jersey Woman   
20211025ecoalf24                                    Pino Round Woman Jersey   
20211025ecoalf25                                          Riaza Woman Dress   
20211025ecoalf26                                           Val Sleeve Woman   
20211025ecoalf27                               Vielha Turtle Seamless Woman   
20211025ecoalf28                                Vielha Round Seamless Woman   
20211025ecoalf29                                      Tormes Woman Cardigan   
20211025ecoalf30                                         Cea Oversize Woman   
20211025ecoalf31                                          Inma Jersey Woman   
20211025ecoalf32                                         Tera Jacket  Woman   
20211025ecoalf33                                    Baiona Woman Sweatshirt   
20211025ecoalf34                                    Llanes Because Woman...   
20211025ecoalf35                                         Basic Woman Hoodie   
20211025ecoalf36                                          Aldan Woman Sweat   
20211025ecoalf37                                   Getaria Woman Sweatshirt   
20211025ecoalf38                                   Bolonia Woman Sweatshirt   
20211025ecoalf39                                 Cudillero Woman Sweatshirt   
20211025ecoalf40                                  Fornells Woman Sweatshirt   
20211025ecoalf41                             Llanes Choice Woman Sweatshirt   
20211025ecoalf42                                      Lulu Woman Sweatshirt   
20211025ecoalf43                                Acacia Woman Long Sleeve...   
20211025ecoalf44                                        Lavanda Shirt Woman   
20211025ecoalf45                                           Wolf Shirt Woman   
20211025ecoalf46                                  Magnolia Long Shirt Woman   
20211025ecoalf47                                Cortegana Woman Long Sleeve   
20211025ecoalf48                                      Because Woman T-Shirt   
20211025ecoalf49                  

In [ ]:
combined_table.to_csv('combined_table_new.csv')

In [ ]:
# Other trial and error attemps

In [ ]:
combined_table['image_link_color'][1200]

'https://cdn.nudiejeans.com/img/Grim-Tim-Dry-Deep-Selvage-113292-05_400x400.jpg'

In [ ]:
dic = {'color':combined_table['image_link_color'][1200]}

In [ ]:
dic

{'color': 'https://cdn.nudiejeans.com/img/Grim-Tim-Dry-Deep-Selvage-113292-05_400x400.jpg'}

In [ ]:
for item in dic.items():
    print(item)

('color', 'https://cdn.nudiejeans.com/img/Grim-Tim-Dry-Deep-Selvage-113292-05_400x400.jpg')


In [ ]:
page = BeautifulSoup(requests.get("https://ecoalf.com/en/women-100").content,'lxml')

In [ ]:
category_class = page.find_all('div',class_="elementor-iqit-banner")

In [ ]:
href = page.find_all('div',class_="elementor-iqit-banner")[9].find('a').get('href')

In [ ]:
"de" in href

True

In [ ]:
if "de" in href:
    href = href.replace("de", "en")

In [ ]:
href

'https://ecoalf.com/en/vestidos-y-faldas-185'

In [ ]:
len(category_class)

20

In [ ]:
cat_dict = {}
for item in category_class:
    try:
        c = item.find('div').get_text()
    except:
        t = None
    l = item.find('a').get('href')
    cat_dict[str(c)]=l

In [ ]:
cat_dict

{'Jackets and coats': 'https://ecoalf.com/en/abrigos-y-chaquetas-120',
 'knitwear & sweaters': 'https://ecoalf.com/en/punto-y-jerseys-160',
 'sweatshirts': 'https://ecoalf.com/en/sudaderas-516',
 'SHIRTS': 'https://ecoalf.com/en/camisas-140',
 't-shirts': 'https://ecoalf.com/en/camisetas-110',
 'pants': 'https://ecoalf.com/en/pantalones-150',
 'skirts &dresses': 'https://ecoalf.com/en/ecoalf-1-0-new-premium-line-561',
 'YOGA': 'https://ecoalf.com/en/yoga-563',
 'Because THERE IS NO  PLANET B® COLLECTION': 'https://ecoalf.com/en/coleccion-because-503'}

In [ ]:
text

['Jackets and coats',
 'knitwear & sweaters',
 'sweatshirts',
 'SHIRTS',
 't-shirts',
 'pants',
 'skirts &dresses',
 'YOGA',
 'Because THERE IS NO  PLANET B® COLLECTION']

In [ ]:
page = BeautifulSoup(requests.get("https://ecoalf.com/en/abrigos-y-chaquetas-120").content,'lxml')

In [ ]:
product_class = page.find_all('div',class_="thumbnail-container")
len(product_class)

77

In [ ]:
product_class[0].find("img").get("alt")

'Lenox Long Woman'

In [ ]:
product_dic = {}
for item in product_class:
    try:
        # Retrieve product name
        p = item.find("img").get("alt")
    except:
        p = None
    # Retrieve product link
    l = item.find('a').get('href')
    if "women" in l:
        # Store the name-link pair in category dictionary
        product_dic[str(p)]=l

In [ ]:
product_dic

{'Lenox Long Woman': 'https://ecoalf.com/en/women/2120291-lenoxalf-long-detachable-vest-woman',
 'Asp Jacket Woman': 'https://ecoalf.com/en/women/2120227-asp-jacket-woman',
 'Marangu Jacket Woman': 'https://ecoalf.com/en/women/2120309-marangu-jacket-woman',
 'Amu New Jacket Woman': 'https://ecoalf.com/en/women/2120202-amu-new-jacket-woman',
 'Gedre Jacket Woman': 'https://ecoalf.com/en/women/2120261-gedre-jacket-woman',
 'Glacier Jacket Woman': 'https://ecoalf.com/en/women/2120266-glacier-jacket-woman',
 'Mandu Jacket Woman': 'https://ecoalf.com/en/women/2120300-mandu-jacket-woman',
 'Marangu Vest Woman': 'https://ecoalf.com/en/women/2120314-marangu-vest-woman',
 'Mulhacen Woman Jacket': 'https://ecoalf.com/en/women/2120321-mulhacen-woman-jacket',
 'Noir Reversible Jacket Woman': 'https://ecoalf.com/en/women/2120325-noir-reversible-jacket-woman',
 'Uma Jacket Woman': 'https://ecoalf.com/en/women/2120339-uma-jacket-woman',
 'Sarrau Corduroy Jacket Woman': 'https://ecoalf.com/en/women/21

In [ ]:
page = BeautifulSoup(requests.get('https://ecoalf.com/en/women/2120290-lenoxalf-long-detachable-vest-woman').content,'lxml')

In [ ]:
price = page.find('span', class_="product-price").get_text()

In [ ]:
price = price.split('$')[1]
f'USD {price}'

'USD 115.00'

In [ ]:
page = BeautifulSoup(requests.get('https://ecoalf.com/de/damen/2120376-riaza-woman-dress').content,'lxml')

In [ ]:
price=page.find('span', class_="product-price").get_text()

In [ ]:
price.split('$')

['185,00\xa0', '']

In [ ]:
color_class = page.find('div', class_="block-content d-flex justify-content-center justify-content-md-start mb-2 mt-3").find_all('a')

In [ ]:
# Create an empty image_link_color dictionary
image_link_color = {}
color = []
for item in color_class:
    link = item.get('href')
    image = BeautifulSoup(requests.get(link).content,'lxml').find('div', class_="product-lmage-large swiper-slide").find('a').get('href')
    c = item.get('title').strip()
    color.append(c)
    image_link_color[str(c)]=image

In [ ]:
image_link_color

{'armygreen': 'https://ecoalf.com/26343-thickbox_default/lenoxalf-long-detachable-vest-woman.jpg',
 'ash': 'https://ecoalf.com/26349-thickbox_default/lenoxalf-long-detachable-vest-woman.jpg',
 'darkbronze': 'https://ecoalf.com/26358-thickbox_default/lenoxalf-long-detachable-vest-woman.jpg',
 'black': 'https://ecoalf.com/26362-thickbox_default/lenoxalf-long-detachable-vest-woman.jpg'}

In [ ]:
json.dumps(image_link_color)

'{"armygreen": "https://ecoalf.com/en/women/2120288-9903-lenoxalf-long-detachable-vest-woman#/7-talla-l", "ash": "https://ecoalf.com/en/women/2120289-9908-lenoxalf-long-detachable-vest-woman#/7-talla-l", "darkbronze": "https://ecoalf.com/en/women/2120290-9913-lenoxalf-long-detachable-vest-woman#/7-talla-l", "black": "https://ecoalf.com/en/women/2120291-9918-lenoxalf-long-detachable-vest-woman#/7-talla-l"}'

In [ ]:
page.find('div', class_="product-lmage-large swiper-slide").find('a').get('href')

'https://ecoalf.com/18408-thickbox_default/abrigo-madison-.jpg'

In [ ]:
page = BeautifulSoup(requests.get('https://ecoalf.com/en/inicio/1920479-camiseta-mariela-').content,'lxml')

In [ ]:
page.find('div',class_="nomcolor text-capitalize mb-4 text-center text-md-left").get_text()

'greymelange'

In [ ]:
page.find('div', class_="product-lmage-large swiper-slide").find('a').get('href')

'https://ecoalf.com/9272-thickbox_default/camiseta-mariela-.jpg'

In [ ]:
# Create an empty image_link_color dictionary
image_link_color = {}
color = []
for item in color_class:
    link = item.get('href')
    c = item.get('title').strip()
    color.append(c)
    image_link_color[str(c)]=link

In [ ]:
image_link_color

{'armygreen': 'https://ecoalf.com/en/women/2120288-9903-lenoxalf-long-detachable-vest-woman#/7-talla-l',
 'ash': 'https://ecoalf.com/en/jackets-and-coats/2120289-9908-lenoxalf-long-detachable-vest-woman#/7-talla-l',
 'darkbronze': 'https://ecoalf.com/en/women/2120290-9913-lenoxalf-long-detachable-vest-woman#/7-talla-l',
 'black': 'https://ecoalf.com/en/women/2120291-9918-lenoxalf-long-detachable-vest-woman#/7-talla-l'}

In [ ]:
size_class = page.find_all('li',class_="input-container float-left")
size_class

[<li class="input-container float-left">
 <input class="input-radio" data-product-attribute="1" data-product-size="XS" name="group[1]" type="radio" value="11"/>
 <span class="radio-label">XS</span>
 </li>,
 <li class="input-container float-left">
 <input class="input-radio" data-product-attribute="1" data-product-size="S" name="group[1]" type="radio" value="10"/>
 <span class="radio-label">S</span>
 </li>,
 <li class="input-container float-left">
 <input class="input-radio" data-product-attribute="1" data-product-size="M" name="group[1]" type="radio" value="6"/>
 <span class="radio-label">M</span>
 </li>,
 <li class="input-container float-left">
 <input checked="checked" class="input-radio" data-product-attribute="1" data-product-size="L" name="group[1]" type="radio" value="7"/>
 <span class="radio-label">L</span>
 </li>,
 <li class="input-container float-left">
 <input class="input-radio" data-product-attribute="1" data-product-size="XL" name="group[1]" type="radio" value="8"/>
 <span

In [ ]:
size_class[0].find('span').get_text()

'XS'

In [ ]:
# Create an empty size list
size = []
for item in size_class:
    s = item.find('span').get_text()
    size.append(s)

In [ ]:
size

['XS', 'S', 'M', 'L', 'XL']

In [ ]:
json.dumps(size)

'["XS", "S", "M", "L", "XL"]'

In [ ]:
description = page.find('div',class_="product-description text-left").find('div',class_="rte-content").get_text().strip()
description

'The Lenox coat is made with recycled polyester, making it a sustainable and very comfortable, warm and ultralight coat. An essential garment for this winter.'

In [ ]:
scrapped_date = datetime.today().strftime('%Y-%m-%d')
scrapped_date

'2021-10-06'

In [ ]:
details = page.find('div', class_="product-description-short rte-content").find_all('li')
details

[<li>Women's coat</li>,
 <li>Turtle neck</li>,
 <li>Hood</li>,
 <li>Zip closure</li>,
 <li>Main fabric: 100% Recycled polyester </li>,
 <li>Lining: 100% Recycled polyester</li>,
 <li>Fill: 100% Polyester (Fellex®)</li>,
 <li>This item contains bluesign® APPROVED fabrics</li>,
 <li>PFC-free</li>,
 <li>Vegan</li>]

In [ ]:
"Main fabric" in detail[4].get_text()

True

In [ ]:
detail[4].get_text().strip().split("Main fabric: ")[1].split(" / ")

['100% Recycled polyester']

In [ ]:
test = "Main fabric: 40% Recycled polyester / 50% Organic cotton / 50% Recycled wool / 5% Recycled cotton"

In [ ]:
materials = test.split("Main fabric: ")[1].split(" / ")
materials

['40% Recycled polyester',
 '50% Organic cotton',
 '50% Recycled wool',
 '5% Recycled cotton']

In [ ]:
materials[0].split('%')

['40', ' Recycled polyester']

In [ ]:
pct = materials[0].split('%')[0]

In [ ]:
f'{pct}%'

'100%%'

In [ ]:
# Create an empty product_material dictionary
product_material = {}
for item in details:
    text = item.get_text()
    if "Main fabric" in text:
        materials = text.strip().split("Main fabric: ")[1].split(" / ")
        for item in materials:
            pct = item.split('%')[0]
            pct = f'{pct}%'
            mtr = item.split('%')[1]
            product_material[str(mtr)]=pct

In [ ]:
json.dumps(product_material)

'{" Recycled polyester": "100%"}'

In [ ]:
page = BeautifulSoup(requests.get('https://ecoalf.com/de/damen/2120192-noja-dress-woman').content,'lxml')

In [ ]:
page.find('div',class_="nomcolor text-capitalize mb-4 text-center text-md-left").get_text()

'whitesand'

In [ ]:
i = [2]
b = [1,2,3]

In [ ]:
a = i.append(b)

In [ ]:
print(a)

None


In [ ]:
page = BeautifulSoup(requests.get('https://ecoalf.com/en/sneakers-270').content,'lxml')

In [ ]:
page.find_all('div',class_="thumbnail-container")[0]

<div class="thumbnail-container">
<a class="thumbnail product-thumbnail" href="https://ecoalf.com/en/men/2120623-tenis-sneakers-man">
<img alt="Prince Sneakers Man" class="img-fluid js-lazy-product-image lazy-product-image product-thumbnail-first" data-full-size-image-url="https://ecoalf.com/23496-thickbox_default/tenis-sneakers-man.jpg" data-src="https://ecoalf.com/23496-home_default/tenis-sneakers-man.jpg" height="1800" src="data:image/svg+xml,%3Csvg xmlns='http://www.w3.org/2000/svg' viewBox='0 0 1200 1800'%3E%3C/svg%3E" width="1200"/>
<img alt="Prince Sneakers Man 2" class="img-fluid js-lazy-product-image lazy-product-image product-thumbnail-second" data-src="https://ecoalf.com/23498-home_default/tenis-sneakers-man.jpg" height="1800" src="data:image/svg+xml,%3Csvg xmlns='http://www.w3.org/2000/svg' viewBox='0 0 1200 1800'%3E%3C/svg%3E" width="1200"/>
</a>
</div>